In [214]:
reset -fs

In [215]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import numpy as np
import pandas as pd                                 #used
import datetime                                     #used
from scipy import stats
import statsmodels.formula.api as smf               #used
import statsmodels.api as sms
import seaborn as sns
from sklearn.model_selection import KFold           #used
from scipy.ndimage.filters import gaussian_filter
import plotly.express as px                         #used

%matplotlib inline

In [216]:
houses = pd.read_csv('King_County_House_prices_dataset.csv')

In [217]:
houses['month_sold'] = pd.DatetimeIndex(houses['date']).month

In [218]:
houses['dol_per_sqft'] = houses.price / houses.sqft_living

In [219]:
houses.sqft_basement.replace('?',0.0, inplace=True)
houses['sqft_basement'] = houses.sqft_basement.astype('float64')
houses['waterfront'] = houses.waterfront.astype('category')
houses['condition'] = houses.condition.astype('category')
houses['grade'] = houses.grade.astype('category')
houses['zipcode'] = houses.zipcode.astype('category')

In [220]:
houses.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21597 entries, 0 to 21596
Data columns (total 23 columns):
id               21597 non-null int64
date             21597 non-null object
price            21597 non-null float64
bedrooms         21597 non-null int64
bathrooms        21597 non-null float64
sqft_living      21597 non-null int64
sqft_lot         21597 non-null int64
floors           21597 non-null float64
waterfront       19221 non-null category
view             21534 non-null float64
condition        21597 non-null category
grade            21597 non-null category
sqft_above       21597 non-null int64
sqft_basement    21597 non-null float64
yr_built         21597 non-null int64
yr_renovated     17755 non-null float64
zipcode          21597 non-null category
lat              21597 non-null float64
long             21597 non-null float64
sqft_living15    21597 non-null int64
sqft_lot15       21597 non-null int64
month_sold       21597 non-null int64
dol_per_sqft     21597 non

In [221]:
dummies_waterfront = pd.get_dummies(data=houses.waterfront, prefix='waterfront', drop_first=True)
dummies_waterfront.head()

waterfront_1.0
0               0
1               0
2               0
3               0
4               0

In [222]:
dummies_condition = pd.get_dummies(data=houses.condition,prefix='condition', drop_first=True)
dummies_condition.head()

condition_2  condition_3  condition_4  condition_5
0            0            1            0            0
1            0            1            0            0
2            0            1            0            0
3            0            0            0            1
4            0            1            0            0

In [223]:
dummies_grade = pd.get_dummies(data=houses.grade,prefix='grade', drop_first=True)
dummies_grade.head()

grade_4  grade_5  grade_6  grade_7  grade_8  grade_9  grade_10  grade_11  \
0        0        0        0        1        0        0         0         0   
1        0        0        0        1        0        0         0         0   
2        0        0        1        0        0        0         0         0   
3        0        0        0        1        0        0         0         0   
4        0        0        0        0        1        0         0         0   

   grade_12  grade_13  
0         0         0  
1         0         0  
2         0         0  
3         0         0  
4         0         0

In [224]:
houses = houses.join(dummies_waterfront)
houses = houses.join(dummies_condition)
houses = houses.join(dummies_grade)

In [225]:
houses.head(2)

id        date     price  bedrooms  bathrooms  sqft_living  \
0  7129300520  10/13/2014  221900.0         3       1.00         1180   
1  6414100192   12/9/2014  538000.0         3       2.25         2570   

   sqft_lot  floors waterfront  view  ... grade_4 grade_5  grade_6  grade_7  \
0      5650     1.0        NaN   0.0  ...       0       0        0        1   
1      7242     2.0        0.0   0.0  ...       0       0        0        1   

   grade_8  grade_9 grade_10  grade_11  grade_12  grade_13  
0        0        0        0         0         0         0  
1        0        0        0         0         0         0  

[2 rows x 38 columns]

In [226]:
smf.ols(formula='price ~ sqft_living + view + condition + grade +  zipcode + sqft_living15', data=houses).fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                  price   R-squared:                       0.812
Model:                            OLS   Adj. R-squared:                  0.811
Method:                 Least Squares   F-statistic:                     1074.
Date:                Mon, 08 Jun 2020   Prob (F-statistic):               0.00
Time:                        12:10:35   Log-Likelihood:            -2.8845e+05
No. Observations:               21534   AIC:                         5.771e+05
Df Residuals:                   21447   BIC:                         5.778e+05
Df Model:                          86                                         
Covariance Type:            nonrobust                                         
====================================================================================
                       coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------
Intercept         3.392e+04   1.63e+05      0.209      0.835   -2.85e+05    3.53e+05
condition[T.2]    6.415e+04   3.22e+04      1.994      0.046    1076.226    1.27e+05
condition[T.3]    6.977e+04   2.99e+04      2.332      0.020    1.11e+04    1.28e+05
condition[T.4]    9.375e+04      3e+04      3.130      0.002     3.5e+04    1.52e+05
condition[T.5]    1.412e+05   3.01e+04      4.689      0.000    8.22e+04       2e+05
grade[T.4]       -1.255e+05   1.63e+05     -0.772      0.440   -4.44e+05    1.93e+05
grade[T.5]       -1.539e+05    1.6e+05     -0.962      0.336   -4.67e+05     1.6e+05
grade[T.6]       -1.643e+05    1.6e+05     -1.029      0.303   -4.77e+05    1.49e+05
grade[T.7]       -1.673e+05    1.6e+05     -1.048      0.295    -4.8e+05    1.46e+05
grade[T.8]       -1.454e+05    1.6e+05     -0.911      0.362   -4.58e+05    1.68e+05
grade[T.9]        -6.68e+04    1.6e+05     -0.418      0.676    -3.8e+05    2.46e+05
grade[T.10]       7.029e+04    1.6e+05      0.440      0.660   -2.43e+05    3.84e+05
grade[T.11]       2.858e+05    1.6e+05      1.786      0.074   -2.79e+04    5.99e+05
grade[T.12]       7.146e+05   1.61e+05      4.442      0.000    3.99e+05    1.03e+06
grade[T.13]       1.803e+06   1.66e+05     10.844      0.000    1.48e+06    2.13e+06
zipcode[T.98002]  8936.4424   1.41e+04      0.633      0.527   -1.88e+04    3.66e+04
zipcode[T.98003] -8259.9082   1.27e+04     -0.650      0.516   -3.32e+04    1.67e+04
zipcode[T.98004]   7.69e+05   1.24e+04     61.830      0.000    7.45e+05    7.93e+05
zipcode[T.98005]  3.118e+05    1.5e+04     20.764      0.000    2.82e+05    3.41e+05
zipcode[T.98006]  2.341e+05   1.13e+04     20.810      0.000    2.12e+05    2.56e+05
zipcode[T.98007]  2.545e+05   1.59e+04     16.031      0.000    2.23e+05    2.86e+05
zipcode[T.98008]  2.728e+05   1.27e+04     21.481      0.000    2.48e+05    2.98e+05
zipcode[T.98010]  7.141e+04    1.8e+04      3.961      0.000    3.61e+04    1.07e+05
zipcode[T.98011]  1.389e+05   1.42e+04      9.762      0.000    1.11e+05    1.67e+05
zipcode[T.98014]  1.073e+05   1.66e+04      6.456      0.000    7.48e+04     1.4e+05
zipcode[T.98019]  1.043e+05   1.43e+04      7.286      0.000    7.62e+04    1.32e+05
zipcode[T.98022] -1.007e+04   1.35e+04     -0.747      0.455   -3.65e+04    1.64e+04
zipcode[T.98023]  -2.55e+04   1.11e+04     -2.306      0.021   -4.72e+04   -3826.022
zipcode[T.98024]   1.77e+05   1.98e+04      8.931      0.000    1.38e+05    2.16e+05
zipcode[T.98027]  1.668e+05   1.16e+04     14.390      0.000    1.44e+05     1.9e+05
zipcode[T.98028]  1.327e+05   1.27e+04     10.462      0.000    1.08e+05    1.58e+05
zipcode[T.98029]  2.233e+05   1.23e+04     18.106      0.000    1.99e+05    2.47e+05
zipcode[T.98030]  1.023e+04    1.3e+04      0.785      0.432   -1.53e+04    3.58e+04
zipcode[T.98031]  1.856

In [227]:
smf.ols(formula='price ~ sqft_living + view + condition + grade +  zipcode + sqft_living15 + dol_per_sqft', data=houses).fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                  price   R-squared:                       0.908
Model:                            OLS   Adj. R-squared:                  0.908
Method:                 Least Squares   F-statistic:                     2432.
Date:                Mon, 08 Jun 2020   Prob (F-statistic):               0.00
Time:                        12:10:36   Log-Likelihood:            -2.8073e+05
No. Observations:               21534   AIC:                         5.616e+05
Df Residuals:                   21446   BIC:                         5.623e+05
Df Model:                          87                                         
Covariance Type:            nonrobust                                         
====================================================================================
                       coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------
Intercept        -7.716e+05   1.14e+05     -6.780      0.000   -9.95e+05   -5.49e+05
condition[T.2]    1.866e+04   2.25e+04      0.830      0.407   -2.54e+04    6.27e+04
condition[T.3]   -7927.5415   2.09e+04     -0.379      0.705   -4.89e+04    3.31e+04
condition[T.4]   -2815.5780   2.09e+04     -0.134      0.893   -4.39e+04    3.82e+04
condition[T.5]    2.009e+04   2.11e+04      0.954      0.340   -2.12e+04    6.14e+04
grade[T.4]        2.186e+05   1.14e+05      1.924      0.054   -4144.302    4.41e+05
grade[T.5]        2.868e+05   1.12e+05      2.565      0.010    6.77e+04    5.06e+05
grade[T.6]        3.011e+05   1.12e+05      2.697      0.007    8.23e+04     5.2e+05
grade[T.7]        3.116e+05   1.12e+05      2.792      0.005    9.28e+04     5.3e+05
grade[T.8]        3.129e+05   1.12e+05      2.803      0.005    9.41e+04    5.32e+05
grade[T.9]        3.284e+05   1.12e+05      2.941      0.003     1.1e+05    5.47e+05
grade[T.10]       3.882e+05   1.12e+05      3.475      0.001    1.69e+05    6.07e+05
grade[T.11]       4.993e+05   1.12e+05      4.464      0.000     2.8e+05    7.19e+05
grade[T.12]       7.604e+05   1.12e+05      6.763      0.000     5.4e+05    9.81e+05
grade[T.13]       1.554e+06   1.16e+05     13.374      0.000    1.33e+06    1.78e+06
zipcode[T.98002]  2.289e+04   9872.292      2.318      0.020    3537.137    4.22e+04
zipcode[T.98003] -1.005e+04   8882.217     -1.131      0.258   -2.75e+04    7362.471
zipcode[T.98004]   1.72e+05   9561.736     17.984      0.000    1.53e+05    1.91e+05
zipcode[T.98005]  9323.3643   1.07e+04      0.872      0.383   -1.16e+04    3.03e+04
zipcode[T.98006] -6233.6508   8024.250     -0.777      0.437    -2.2e+04    9494.478
zipcode[T.98007]  1818.6720   1.12e+04      0.162      0.871   -2.02e+04    2.38e+04
zipcode[T.98008]  1.034e+04   9045.023      1.143      0.253   -7393.349    2.81e+04
zipcode[T.98010] -3.206e+04   1.26e+04     -2.540      0.011   -5.68e+04   -7322.814
zipcode[T.98011] -1.466e+04   9993.204     -1.467      0.142   -3.42e+04    4930.788
zipcode[T.98014] -2.169e+04   1.17e+04     -1.861      0.063   -4.45e+04    1149.764
zipcode[T.98019] -1.466e+04      1e+04     -1.461      0.144   -3.43e+04    5010.607
zipcode[T.98022] -2.229e+04   9421.487     -2.366      0.018   -4.08e+04   -3825.758
zipcode[T.98023] -1.425e+04   7729.657     -1.844      0.065   -2.94e+04     896.383
zipcode[T.98024] -1.608e+04   1.39e+04     -1.156      0.248   -4.33e+04    1.12e+04
zipcode[T.98027] -2.359e+04   8199.617     -2.877      0.004   -3.97e+04   -7520.013
zipcode[T.98028] -1.104e+04   8919.150     -1.237      0.216   -2.85e+04    6445.693
zipcode[T.98029]  2938.6938   8741.927      0.336      0.737   -1.42e+04    2.01e+04
zipcode[T.98030] -3214.5641   9106.734     -0.353      0.724   -2.11e+04    1.46e+04
zipcode[T.98031] -2610.

In [228]:
kf = KFold(n_splits=5, shuffle=True)
for train,test in kf.split(houses):
    print('%s %s' % (train,test))

[    1     2     3 ... 21591 21594 21595] [    0     8    13 ... 21592 21593 21596]
[    0     1     2 ... 21594 21595 21596] [    3    12    18 ... 21586 21589 21591]
[    0     1     2 ... 21594 21595 21596] [    4    14    15 ... 21580 21587 21590]
[    0     2     3 ... 21593 21594 21596] [    1     5     6 ... 21581 21584 21595]
[    0     1     3 ... 21593 21595 21596] [    2    17    19 ... 21577 21582 21594]


In [234]:
print(test)

[    2    17    19 ... 21577 21582 21594]


In [233]:
smf.ols(formula='price ~ sqft_living + view + condition + grade +  zipcode + sqft_living15 + dol_per_sqft', data=houses).fit().summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                  price   R-squared:                       0.908
Model:                            OLS   Adj. R-squared:                  0.908
Method:                 Least Squares   F-statistic:                     2432.
Date:                Mon, 08 Jun 2020   Prob (F-statistic):               0.00
Time:                        12:13:28   Log-Likelihood:            -2.8073e+05
No. Observations:               21534   AIC:                         5.616e+05
Df Residuals:                   21446   BIC:                         5.623e+05
Df Model:                          87                                         
Covariance Type:            nonrobust                                         
====================================================================================
                       coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------------
Intercept        -7.716e+05   1.14e+05     -6.780      0.000   -9.95e+05   -5.49e+05
condition[T.2]    1.866e+04   2.25e+04      0.830      0.407   -2.54e+04    6.27e+04
condition[T.3]   -7927.5415   2.09e+04     -0.379      0.705   -4.89e+04    3.31e+04
condition[T.4]   -2815.5780   2.09e+04     -0.134      0.893   -4.39e+04    3.82e+04
condition[T.5]    2.009e+04   2.11e+04      0.954      0.340   -2.12e+04    6.14e+04
grade[T.4]        2.186e+05   1.14e+05      1.924      0.054   -4144.302    4.41e+05
grade[T.5]        2.868e+05   1.12e+05      2.565      0.010    6.77e+04    5.06e+05
grade[T.6]        3.011e+05   1.12e+05      2.697      0.007    8.23e+04     5.2e+05
grade[T.7]        3.116e+05   1.12e+05      2.792      0.005    9.28e+04     5.3e+05
grade[T.8]        3.129e+05   1.12e+05      2.803      0.005    9.41e+04    5.32e+05
grade[T.9]        3.284e+05   1.12e+05      2.941      0.003     1.1e+05    5.47e+05
grade[T.10]       3.882e+05   1.12e+05      3.475      0.001    1.69e+05    6.07e+05
grade[T.11]       4.993e+05   1.12e+05      4.464      0.000     2.8e+05    7.19e+05
grade[T.12]       7.604e+05   1.12e+05      6.763      0.000     5.4e+05    9.81e+05
grade[T.13]       1.554e+06   1.16e+05     13.374      0.000    1.33e+06    1.78e+06
zipcode[T.98002]  2.289e+04   9872.292      2.318      0.020    3537.137    4.22e+04
zipcode[T.98003] -1.005e+04   8882.217     -1.131      0.258   -2.75e+04    7362.471
zipcode[T.98004]   1.72e+05   9561.736     17.984      0.000    1.53e+05    1.91e+05
zipcode[T.98005]  9323.3643   1.07e+04      0.872      0.383   -1.16e+04    3.03e+04
zipcode[T.98006] -6233.6508   8024.250     -0.777      0.437    -2.2e+04    9494.478
zipcode[T.98007]  1818.6720   1.12e+04      0.162      0.871   -2.02e+04    2.38e+04
zipcode[T.98008]  1.034e+04   9045.023      1.143      0.253   -7393.349    2.81e+04
zipcode[T.98010] -3.206e+04   1.26e+04     -2.540      0.011   -5.68e+04   -7322.814
zipcode[T.98011] -1.466e+04   9993.204     -1.467      0.142   -3.42e+04    4930.788
zipcode[T.98014] -2.169e+04   1.17e+04     -1.861      0.063   -4.45e+04    1149.764
zipcode[T.98019] -1.466e+04      1e+04     -1.461      0.144   -3.43e+04    5010.607
zipcode[T.98022] -2.229e+04   9421.487     -2.366      0.018   -4.08e+04   -3825.758
zipcode[T.98023] -1.425e+04   7729.657     -1.844      0.065   -2.94e+04     896.383
zipcode[T.98024] -1.608e+04   1.39e+04     -1.156      0.248   -4.33e+04    1.12e+04
zipcode[T.98027] -2.359e+04   8199.617     -2.877      0.004   -3.97e+04   -7520.013
zipcode[T.98028] -1.104e+04   8919.150     -1.237      0.216   -2.85e+04    6445.693
zipcode[T.98029]  2938.6938   8741.927      0.336      0.737   -1.42e+04    2.01e+04
zipcode[T.98030] -3214.5641   9106.734     -0.353      0.724   -2.11e+04    1.46e+04
zipcode[T.98031] -2610.

In [117]:
fig = px.scatter_mapbox(houses, lat="lat", lon="long", hover_name="id",hover_data=['dol_per_sqft','price','sqft_living','yr_built','yr_renovated'],
                        color='dol_per_sqft', zoom=3, height=300)
fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [167]:
houses.corr()

id     price  bedrooms  bathrooms  sqft_living  \
id              1.000000 -0.016772  0.001150   0.005162    -0.012241   
price          -0.016772  1.000000  0.308787   0.525906     0.701917   
bedrooms        0.001150  0.308787  1.000000   0.514508     0.578212   
bathrooms       0.005162  0.525906  0.514508   1.000000     0.755758   
sqft_living    -0.012241  0.701917  0.578212   0.755758     1.000000   
sqft_lot       -0.131911  0.089876  0.032471   0.088373     0.173453   
floors          0.018608  0.256804  0.177944   0.502582     0.353953   
waterfront     -0.004176  0.276295 -0.002386   0.067282     0.110230   
view            0.011592  0.395734  0.078523   0.186451     0.282532   
condition      -0.023803  0.036056  0.026496  -0.126479    -0.059445   
grade           0.008188  0.667951  0.356563   0.665838     0.762779   
sqft_above     -0.010799  0.605368  0.479386   0.686668     0.876448   
sqft_basement  -0.004359  0.321108  0.297229   0.278485     0.428660   
yr_built        0.021617  0.053953  0.155670   0.507173     0.318152   
yr_renovated   -0.012010  0.129599  0.018495   0.051050     0.055660   
zipcode        -0.008211 -0.053402 -0.154092  -0.204786    -0.199802   
lat            -0.001798  0.306692 -0.009951   0.024280     0.052155   
long            0.020672  0.022036  0.132054   0.224903     0.241214   
sqft_living15  -0.002701  0.585241  0.393406   0.569884     0.756402   
sqft_lot15     -0.138557  0.082845  0.030690   0.088303     0.184342   
month_sold     -0.011572 -0.009928 -0.001046   0.007543     0.012112   
dol_per_sqft   -0.005244  0.556056 -0.205905  -0.090285    -0.091167   
waterfront_1.0 -0.003599  0.264306 -0.002127   0.063629     0.104637   
condition_2    -0.012780 -0.051432 -0.049463  -0.075933    -0.063984   
condition_3     0.031000  0.006948  0.005210   0.190790     0.102061   
condition_4    -0.025497 -0.030759 -0.009841  -0.166756    -0.083850   
condition_5    -0.009534  0.057531  0.027500  -0.034765    -0.018284   
grade_4        -0.002903 -0.031618 -0.068012  -0.055599    -0.053935   
grade_5        -0.025640 -0.084549 -0.113175  -0.138740    -0.127198   
grade_6        -0.015476 -0.209463 -0.239492  -0.366185    -0.312486   
grade_7        -0.015575 -0.316053 -0.104791  -0.313457    -0.358915   
grade_8         0.042285  0.004576  0.073140   0.189426     0.071115   
grade_9         0.009121  0.235859  0.160294   0.264756     0.318499   
grade_10       -0.014390  0.340944  0.135766   0.272635     0.369228   
grade_11       -0.019837  0.357589  0.116596   0.247293     0.345964   
grade_12       -0.015084  0.291068  0.062257   0.159734     0.238136   
grade_13       -0.003880  0.211806  0.039026   0.095118     0.144424   

                sqft_lot    floors  waterfront      view  condition  ...  \
id             -0.131911  0.018608   -0.004176  0.011592  -0.023803  ...   
price           0.089876  0.256804    0.276295  0.395734   0.036056  ...   
bedrooms        0.032471  0.177944   -0.002386  0.078523   0.026496  ...   
bathrooms       0.088373  0.502582    0.067282  0.186451  -0.126479  ...   
sqft_living     0.173453  0.353953    0.110230  0.282532  -0.059445  ...   
sqft_lot        1.000000 -0.004814    0.023143  0.075298  -0.008830  ...   
floors         -0.004814  1.000000    0.021883  0.028436  -0.264075  ...   
waterfront      0.023143  0.021883    1.000000  0.406654   0.017642  ...   
view            0.075298  0.028436    0.406654  1.000000   0.045735  ...   
condition      -0.008830 -0.264075    0.017642  0.045735   1.000000  ...   
grade           0.114731  0.458794    0.087383  0.249727  -0.146896  ...   
sqft_above      0.184139  0.523989    0.075463  0.166299  -0.158904  ...   
sqft_basement   0.015031 -0.241866    0.088213  0.271689   0.168482  ...   
yr_built        0.052946  0.489193   -0.026079 -0.054564  -0.361592  ...   
yr_renovated    0.004513  0.003535    0.087244  0.100964  -0.061858  ...   
zipcode        -0.129586 -0.059541    0.031057  0.085277   0.002888  